# Clube do Livro - Cap. 06 
# Agrupamentos 

In [0]:
spark.conf.set("spark.sql.legacy.timeParserPolicy","LEGACY")

In [0]:
path = "/databricks-datasets/definitive-guide/data/retail-data/all/*.csv"

df = ( 
        spark.read
            .format('csv')
            .option('header', 'true')
            .option('inferSchema', 'true')
            .load(path)
            .coalesce(5)

)

df.cache().count()
df.printSchema()
df.createOrReplaceTempView('dfTable')

root
 |-- InvoiceNo: string (nullable = true)
 |-- StockCode: string (nullable = true)
 |-- Description: string (nullable = true)
 |-- Quantity: integer (nullable = true)
 |-- InvoiceDate: string (nullable = true)
 |-- UnitPrice: double (nullable = true)
 |-- CustomerID: integer (nullable = true)
 |-- Country: string (nullable = true)



In [0]:
from pyspark.sql.functions import count, countDistinct, approxCountDistinct, first, last, min, max, sum,sumDistinct, avg, col


display(
  df.select(
    count('*').alias('countAll'),
    count(col('CustomerID')).alias('countCustID'), # count not null 
    countDistinct(col('customerID')).alias('countDistCustID'),
    approxCountDistinct(col('customerID'), 0.1 ).alias('countApproxCustID'),
    first(col('customerID')).alias('firstRow'),
    last(col('customerID')).alias('lastRow'),
    min(col('customerID')).alias('minCustID'),
    max(col('customerID')).alias('maxRow'),
    sum('Quantity').alias('sumQtd'),
    sumDistinct(col('Quantity')).alias('sumDistQtd'),
    avg(col('Quantity')).alias('avgQnt')
  )
)

/databricks/spark/python/pyspark/sql/functions.py:3675: FutureWarning: Deprecated in 2.1, use approx_count_distinct instead.
  warnings.warn("Deprecated in 2.1, use approx_count_distinct instead.", FutureWarning)
/databricks/spark/python/pyspark/sql/functions.py:977: FutureWarning: Deprecated in 3.2, use sum_distinct instead.
  warnings.warn("Deprecated in 3.2, use sum_distinct instead.", FutureWarning)


countAll countCustID countDistCustID countApproxCustID firstRow lastRow minCustID maxRow sumQtd sumDistQtd avgQnt 541909 406829 4372 4336 17850 12680 12346 18287 5176450 29310 9.55224954743324

In [0]:
# Recommendation : When applying AVG(), use COALESCE to convert NULL values into zeros. This way, we will obtain the correct average, since the AVG() function ignores NULL values.

df_avg = spark.sql("""
            select 1 as col1 
            union all 
            select 2 as col1
            union all 
            select 3 as col1
            union all 
            select null as col1
             """)

df_avg.selectExpr(
    "count(col1) as count", # not null
    "sum(col1) as sum",
    "avg(col1) as avg"  # not null 
).display()

count sum avg 3 6 2.0

In [0]:
from pyspark.sql.functions import collect_set, collect_list

df2 = df.limit(200)


display(
  df2.agg(
      collect_set('Country'), # returns array with distinct values
      collect_list('Country') # return all values
  )
)

collect_set(Country) collect_list(Country) List(France, Australia, United Kingdom) List(United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, France, France, France, France, France, France, France, France, France, France, France, France, France, France, France, France, France, France, France, France, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, United Kingdom, Australia, Australia, Australia)

Window Function

In [0]:
from pyspark.sql.functions import to_date

dfWithDate = (
  df.withColumn( "date", to_date(col('InvoiceDate'), "MM/d/yyyy H:mm"))

)

dfWithDate.createOrReplaceTempView('dfWithDate')

display(dfWithDate.limit(5))

InvoiceNo StockCode Description Quantity InvoiceDate UnitPrice CustomerID Country date 536365 85123A WHITE HANGING HEART T-LIGHT HOLDER 6 12/1/2010 8:26 2.55 17850 United Kingdom 2010-12-01 536365 71053 WHITE METAL LANTERN 6 12/1/2010 8:26 3.39 17850 United Kingdom 2010-12-01 536365 84406B CREAM CUPID HEARTS COAT HANGER 8 12/1/2010 8:26 2.75 17850 United Kingdom 2010-12-01 536365 84029G KNITTED UNION FLAG HOT WATER BOTTLE 6 12/1/2010 8:26 3.39 17850 United Kingdom 2010-12-01 536365 84029E RED WOOLLY HOTTIE WHITE HEART. 6 12/1/2010 8:26 3.39 17850 United Kingdom 2010-12-01

In [0]:
from pyspark.sql import Window
from pyspark.sql.functions import rank, dense_rank, lead

windowSpec = (
    Window
    .partitionBy( "CustomerID", "date").orderBy(col('Quantity').desc())
    .rowsBetween(
        Window.unboundedPreceding,
        Window.currentRow
        )
    )


maxPurchaseQnt = max(col('Quantity')).over(windowSpec)
sumQnt = sum(col('Quantity')).over(windowSpec)
purchaseDenseRank = dense_rank().over(windowSpec)
purchaseRank = rank().over(windowSpec)


display(
    dfWithDate.where( "CustomerID is not NULL")
    .select(
        col('CustomerID'),
        col('date'),
        col('Quantity'),
        maxPurchaseQnt.alias('maxPurchaseQnt'),
        sumQnt.alias('sumQnt'),
        purchaseDenseRank.alias('purchaseDenseRank'),
        purchaseRank.alias('purchaseRank')

    )
)

CustomerID date Quantity maxPurchaseQnt sumQnt purchaseDenseRank purchaseRank 12346 2011-01-18 74215 74215 74215 1 1 12346 2011-01-18 -74215 74215 0 2 2 12347 2010-12-07 36 36 36 1 1 12347 2010-12-07 30 36 66 2 2 12347 2010-12-07 24 36 90 3 3 12347 2010-12-07 12 36 102 4 4 12347 2010-12-07 12 36 114 4 4 12347 2010-12-07 12 36 126 4 4 12347 2010-12-07 12 36 138 4 4 12347 2010-12-07 12 36 150 4 4 12347 2010-12-07 12 36 162 4 4 12347 2010-12-07 12 36 174 4 4 12347 2010-12-07 12 36 186 4 4 12347 2010-12-07 12 36 198 4 4 12347 2010-12-07 12 36 210 4 4 12347 2010-12-07 12 36 222 4 4 12347 2010-12-07 12 36 234 4 4 12347 2010-12-07 12 36 246 4 4 12347 2010-12-07 6 36 252 5 17 12347 2010-12-07 6 36 258 5 17 12347 2010-12-07 6 36 264 5 17 12347 2010-12-07 6 36 270 5 17 12347 2010-12-07 6 36 276 5 17 12347 2010-12-07 6 36 282 5 17 12347 2010-12-07 6 36 288 5 17 12347 2010-12-07 4 36 292 6 24 12347 2010-12-07 4 36 296 6 24 12347 2010-12-07 4 36 300 6 24 12347 2010-12-07 4 36 304 6 24 12347 2010-12-07 4 36 308 6 24 12347 2010-12-07 4 36 312 6 24 12347 2010-12-07 4 36 316 6 24 12347 2010-12-07 3 36 319 7 31 12347 2011-01-26 24 24 24 1 1 12347 2011-01-26 24 24 48 1 1 12347 2011-01-26 24 24 72 1 1 12347 2011-01-26 24 24 96 1 1 12347 2011-01-26 24 24 120 1 1 12347 2011-01-26 24 24 144 1 1 12347 2011-01-26 12 24 156 2 7 12347 2011-01-26 12 24 168 2 7 12347 2011-01-26 12 24 180 2 7 12347 2011-01-26 12 24 192 2 7 12347 2011-01-26 12 24 204 2 7 12347 2011-01-26 12 24 216 2 7 12347 2011-01-26 10 24 226 3 13 12347 2011-01-26 10 24 236 3 13 12347 2011-01-26 10 24 246 3 13 12347 2011-01-26 10 24 256 3 13 12347 2011-01-26 6 24 262 4 17 12347 2011-01-26 6 24 268 4 17 12347 2011-01-26 6 24 274 4 17 12347 2011-01-26 6 24 280 4 17 12347 2011-01-26 4 24 284 5 21 12347 2011-01-26 4 24 288 5 21 12347 2011-01-26 4 24 292 5 21 12347 2011-01-26 4 24 296 5 21 12347 2011-01-26 4 24 300 5 21 12347 2011-01-26 4 24 304 5 21 12347 2011-01-26 4 24 308 5 21 12347 2011-01-26 4 24 312 5 21 12347 2011-01-26 3 24 315 6 29 12347 2011-04-07 240 240 240 1 1 12347 2011-04-07 36 240 276 2 2 12347 2011-04-07 24 240 300 3 3 12347 2011-04-07 24 240 324 3 3 12347 2011-04-07 12 240 336 4 5 12347 2011-04-07 12 240 348 4 5 12347 2011-04-07 12 240 360 4 5 12347 2011-04-07 12 240 372 4 5 12347 2011-04-07 12 240 384 4 5 12347 2011-04-07 12 240 396 4 5 12347 2011-04-07 12 240 408 4 5 12347 2011-04-07 12 240 420 4 5 12347 2011-04-07 8 240 428 5 13 12347 2011-04-07 8 240 436 5 13 12347 2011-04-07 6 240 442 6 15 12347 2011-04-07 6 240 448 6 15 12347 2011-04-07 6 240 454 6 15 12347 2011-04-07 6 240 460 6 15 12347 2011-04-07 4 240 464 7 19 12347 2011-04-07 4 240 468 7 19 12347 2011-04-07 4 240 472 7 19 12347 2011-04-07 4 240 476 7 19 12347 2011-04-07 4 240 480 7 19 12347 2011-04-07 3 240 483 8 24 12347 2011-06-09 36 36 36 1 1 12347 2011-06-09 24 36 60 2 2 12347 2011-06-09 18 36 78 3 3 12347 2011-06-09 12 36 90 4 4 12347 2011-06-09 12 36 102 4 4 12347 2011-06-09 12 36 114 4 4 12347 2011-06-09 12 36 126 4 4 12347 2011-06-09 12 36 138 4 4 12347 2011-06-09 12 36 150 4 4 12347 2011-06-09 8 36 158 5 10 12347 2011-06-09 8 36 166 5 10 12347 2011-06-09 8 36 174 5 10 12347 2011-06-09 4 36 178 6 13 12347 2011-06-09 4 36 182 6 13 12347 2011-06-09 4 36 186 6 13 12347 2011-06-09 4 36 190 6 13 12347 2011-06-09 4 36 194 6 13 12347 2011-06-09 2 36 196 7 18 12347 2011-08-02 36 36 36 1 1 12347 2011-08-02 24 36 60 2 2 12347 2011-08-02 24 36 84 2 2 12347 2011-08-02 24 36 108 2 2 12347 2011-08-02 24 36 132 2 2 12347 2011-08-02 24 36 156 2 2 12347 2011-08-02 16 36 172 3 7 12347 2011-08-02 12 36 184 4 8 12347 2011-08-02 12 36 196 4 8 12347 2011-08-02 12 36 208 4 8 12347 2011-08-02 10 36 218 5 11 12347 2011-08-02 10 36 228 5 11 12347 2011-08-02 8 36 236 6 13 12347 2011-08-02 8 36 244 6 13 12347 2011-08-02 6 36 250 7 15 12347 2011-08-02 4 36 254 8 16 12347 2011-08-02 4 36 258 8 16 12347 2011-08-02 4 36 262 8 16 12347 2011-08-02 4 36 266 8 16 12347 2011-08-02 4 36 270 8 16 12347 2011-08-02 4 36 274 8 16 12347 2011-08-02 

In [0]:
%sql

select 
  CustomerID,
  'date',
  Quantity,
  MAX(quantity) over(partition by CustomerID, 'date' order by Quantity desc rows between unbounded preceding and current row) as max_qnt,
  SUM(quantity) over(partition by CustomerID, 'date' order by Quantity desc rows between unbounded preceding and current row) as sum_qnt,
  dense_rank()  over(partition by CustomerID, 'date' order by Quantity desc rows between unbounded preceding and current row) as dense_rank_qnt,
  rank()        over(partition by CustomerID, 'date' order by Quantity desc rows between unbounded preceding and current row) as rank_qnt
  from dfWithDate
  where CustomerID is not null 

CustomerID date Quantity max_qnt sum_qnt dense_rank_qnt rank_qnt 12346 date 74215 74215 74215 1 1 12346 date -74215 74215 0 2 2 12347 date 240 240 240 1 1 12347 date 48 240 288 2 2 12347 date 36 240 324 3 3 12347 date 36 240 360 3 3 12347 date 36 240 396 3 3 12347 date 36 240 432 3 3 12347 date 36 240 468 3 3 12347 date 36 240 504 3 3 12347 date 30 240 534 4 9 12347 date 24 240 558 5 10 12347 date 24 240 582 5 10 12347 date 24 240 606 5 10 12347 date 24 240 630 5 10 12347 date 24 240 654 5 10 12347 date 24 240 678 5 10 12347 date 24 240 702 5 10 12347 date 24 240 726 5 10 12347 date 24 240 750 5 10 12347 date 24 240 774 5 10 12347 date 24 240 798 5 10 12347 date 24 240 822 5 10 12347 date 24 240 846 5 10 12347 date 24 240 870 5 10 12347 date 24 240 894 5 10 12347 date 24 240 918 5 10 12347 date 24 240 942 5 10 12347 date 24 240 966 5 10 12347 date 24 240 990 5 10 12347 date 24 240 1014 5 10 12347 date 24 240 1038 5 10 12347 date 24 240 1062 5 10 12347 date 24 240 1086 5 10 12347 date 24 240 1110 5 10 12347 date 24 240 1134 5 10 12347 date 24 240 1158 5 10 12347 date 20 240 1178 6 36 12347 date 20 240 1198 6 36 12347 date 20 240 1218 6 36 12347 date 20 240 1238 6 36 12347 date 18 240 1256 7 40 12347 date 18 240 1274 7 40 12347 date 16 240 1290 8 42 12347 date 16 240 1306 8 42 12347 date 12 240 1318 9 44 12347 date 12 240 1330 9 44 12347 date 12 240 1342 9 44 12347 date 12 240 1354 9 44 12347 date 12 240 1366 9 44 12347 date 12 240 1378 9 44 12347 date 12 240 1390 9 44 12347 date 12 240 1402 9 44 12347 date 12 240 1414 9 44 12347 date 12 240 1426 9 44 12347 date 12 240 1438 9 44 12347 date 12 240 1450 9 44 12347 date 12 240 1462 9 44 12347 date 12 240 1474 9 44 12347 date 12 240 1486 9 44 12347 date 12 240 1498 9 44 12347 date 12 240 1510 9 44 12347 date 12 240 1522 9 44 12347 date 12 240 1534 9 44 12347 date 12 240 1546 9 44 12347 date 12 240 1558 9 44 12347 date 12 240 1570 9 44 12347 date 12 240 1582 9 44 12347 date 12 240 1594 9 44 12347 date 12 240 1606 9 44 12347 date 12 240 1618 9 44 12347 date 12 240 1630 9 44 12347 date 12 240 1642 9 44 12347 date 12 240 1654 9 44 12347 date 12 240 1666 9 44 12347 date 12 240 1678 9 44 12347 date 12 240 1690 9 44 12347 date 12 240 1702 9 44 12347 date 12 240 1714 9 44 12347 date 12 240 1726 9 44 12347 date 12 240 1738 9 44 12347 date 12 240 1750 9 44 12347 date 12 240 1762 9 44 12347 date 12 240 1774 9 44 12347 date 12 240 1786 9 44 12347 date 12 240 1798 9 44 12347 date 12 240 1810 9 44 12347 date 12 240 1822 9 44 12347 date 12 240 1834 9 44 12347 date 12 240 1846 9 44 12347 date 12 240 1858 9 44 12347 date 12 240 1870 9 44 12347 date 12 240 1882 9 44 12347 date 12 240 1894 9 44 12347 date 12 240 1906 9 44 12347 date 12 240 1918 9 44 12347 date 12 240 1930 9 44 12347 date 12 240 1942 9 44 12347 date 12 240 1954 9 44 12347 date 12 240 1966 9 44 12347 date 12 240 1978 9 44 12347 date 10 240 1988 10 100 12347 date 10 240 1998 10 100 12347 date 10 240 2008 10 100 12347 date 10 240 2018 10 100 12347 date 10 240 2028 10 100 12347 date 10 240 2038 10 100 12347 date 10 240 2048 10 100 12347 date 10 240 2058 10 100 12347 date 10 240 2068 10 100 12347 date 8 240 2076 11 109 12347 date 8 240 2084 11 109 12347 date 8 240 2092 11 109 12347 date 8 240 2100 11 109 12347 date 8 240 2108 11 109 12347 date 8 240 2116 11 109 12347 date 8 240 2124 11 109 12347 date 8 240 2132 11 109 12347 date 8 240 2140 11 109 12347 date 8 240 2148 11 109 12347 date 8 240 2156 11 109 12347 date 8 240 2164 11 109 12347 date 8 240 2172 11 109 12347 date 8 240 2180 11 109 12347 date 8 240 2188 11 109 12347 date 6 240 2194 12 124 12347 date 6 240 2200 12 124 12347 date 6 240 2206 12 124 12347 date 6 240 2212 12 124 12347 date 6 240 2218 12 124 12347 date 6 240 2224 12 124 12347 date 6 240 2230 12 124 12347 date 6 240 2236 12 124 12347 date 6 240 2242 12 124 12347 date 6 240 2248 12 124 12347 date 6 240 2254 12 124 12347 date 6 240 2260 12 124 12347 date 6 240 2266 12 124 12347 date 6 240 2272 12 124 12347 date 6 240 2278 12 

In [0]:
dfNotNull = dfWithDate.na.drop()
dfNotNull.createOrReplaceTempView('dfNotNull')

In [0]:

%sql 
-- two or more groupings in one table


select 
  customerID,
  null as stockCode,
  sum(Quantity) as qnt
from dfNotNull
group by customerID

union all 

select 
  customerID,
  stockCode,
  sum(Quantity) as qnt
from dfNotNull
group by customerID,stockCode
order by customerID
limit 10 

customerID stockCode qnt 12346 null 0 12346 23166 0 12347 21976 48 12347 22771 12 12347 22699 24 12347 22698 12 12347 21171 12 12347 22728 16 12347 22729 8 12347 23174 4

### A better way to perform this aggregation is by using grouping sets.

In [0]:
%sql

select 
  customerID, 
  stockCode, 
  grouping_id() as aggID, -- This approach identifies the aggregation level.
  sum(quantity) as qnt
from dfNotNull
group by customerID, stockCode
  grouping sets (
    (customerID),
    (customerID,stockCode)
  )
order by customerID,stockCode

customerID stockCode aggID qnt 12346 null 1 0 12346 23166 0 0 12347 null 1 2458 12347 16008 0 24 12347 17021 0 36 12347 20665 0 6 12347 20719 0 40 12347 20780 0 12 12347 20782 0 6 12347 20966 0 10 12347 21035 0 6 12347 21041 0 12 12347 21064 0 30 12347 21154 0 10 12347 21171 0 12 12347 21265 0 24 12347 21578 0 6 12347 21636 0 12 12347 21731 0 72 12347 21791 0 48 12347 21832 0 12 12347 21975 0 48 12347 21976 0 48 12347 22131 0 6 12347 22134 0 12 12347 22195 0 48 12347 22196 0 72 12347 22212 0 6 12347 22252 0 12 12347 22371 0 32 12347 22372 0 8 12347 22374 0 16 12347 22375 0 28 12347 22376 0 12 12347 22417 0 48 12347 22422 0 12 12347 22423 0 15 12347 22432 0 6 12347 22492 0 108 12347 22494 0 12 12347 22497 0 12 12347 22550 0 8 12347 22561 0 12 12347 22621 0 12 12347 22697 0 12 12347 22698 0 12 12347 22699 0 24 12347 22725 0 20 12347 22726 0 16 12347 22727 0 36 12347 22728 0 16 12347 22729 0 8 12347 22771 0 12 12347 22772 0 12 12347 22773 0 12 12347 22774 0 24 12347 22775 0 12 12347 22805 0 12 12347 22821 0 12 12347 22945 0 12 12347 22992 0 24 12347 23076 0 240 12347 23084 0 84 12347 23146 0 16 12347 23147 0 12 12347 23162 0 16 12347 23170 0 12 12347 23171 0 12 12347 23172 0 12 12347 23173 0 4 12347 23174 0 4 12347 23175 0 8 12347 23177 0 16 12347 23271 0 16 12347 23297 0 16 12347 23308 0 48 12347 23316 0 12 12347 23420 0 12 12347 23421 0 12 12347 23422 0 12 12347 23480 0 12 12347 23497 0 12 12347 23503 0 12 12347 23506 0 40 12347 23508 0 40 12347 23552 0 6 12347 47559B 0 30 12347 47567B 0 6 12347 47580 0 6 12347 51014C 0 12 12347 71477 0 12 12347 84558A 0 126 12347 84559A 0 12 12347 84559B 0 12 12347 84625A 0 48 12347 84625C 0 24 12347 84969 0 12 12347 84991 0 72 12347 84992 0 72 12347 84997B 0 6 12347 84997C 0 6 12347 84997D 0 6 12347 85116 0 18 12347 85167B 0 30 12347 85178 0 12 12347 85232D 0 3 12348 null 1 2341 12348 21211 0 72 12348 21213 0 144 12348 21725 0 48 12348 21726 0 24 12348 21967 0 144 12348 21977 0 144 12348 21980 0 144 12348 21981 0 144 12348 21982 0 144 12348 21983 0 144 12348 21985 0 144 12348 22437 0 20 12348 22616 0 72 12348 22951 0 72 12348 22952 0 144 12348 23076 0 72 12348 23077 0 200 12348 23078 0 192 12348 84988 0 48 12348 84991 0 144 12348 84992 0 72 12348 POST 0 9 12349 null 1 631 12349 20685 0 6 12349 20914 0 6 12349 21086 0 12 12349 21136 0 16 12349 21231 0 36 12349 21232 0 36 12349 21411 0 3 12349 21531 0 6 12349 21533 0 3 12349 21535 0 6 12349 21563 0 6 12349 21564 0 6 12349 21787 0 24 12349 22059 0 12 12349 22064 0 12 12349 22070 0 6 12349 22071 0 6 12349 22131 0 6 12349 22195 0 12 12349 22326 0 6 12349 22333 0 8 12349 22423 0 1 12349 22430 0 4 12349 22441 0 8 12349 22553 0 12 12349 22554 0 12 12349 22555 0 12 12349 22556 0 12 12349 22557 0 12 12349 22567 0 12 12349 22601 0 12 12349 22666 0 6 12349 22692 0 4 12349 22704 0 25 12349 22720 0 3 12349 22722 0 4 12349 22832 0 2 12349 22960 0 6 12349 23020 0 1 12349 23108 0 2 12349 23112 0 2 12349 23113 0 3 12349 23198 0 12 12349 23236 0 6 12349 23240 0 6 12349 23253 0 4 12349 23263 0 12 12349 23273 0 12 12349 23283 0 2 12349 23293 0 8 12349 23294 0 8 12349 23295 0 8 12349 23296 0 8 12349 23439 0 12 12349 23460 0 2 12349 23493 0 10 12349 23494 0 3 12349 23497 0 12 12349 23514 0 6 12349 23545 0 25 12349 35970 0 12 12349 37448 0 12 12349 37500 0 12 12349 47504H 0 12 12349 48184 0 6 12349 48185 0 4 12349 48194 0 2 12349 84078A 0 1 12349 84978 0 12 12349 85014A 0 3 12349 85014B 0 3 12349 85053 0 6 12349 POST 0 1 12350 null 1 197 12350 20615 0 12 12350 20652 0 12 12350 21171 0 12 12350 21832 0 12 12350 21864 0 12 12350 21866 0 12 12350 21908 0 12 12350 21915 0 12 12350 22348 0 24 12350 22412 0 12 12350 22551 0 12 12350 22557 0 12 12350 22620 0 12 12350 79066K 0 10 12350 79191C 0 12 12350 84086C 0 6 12350 POST 0 1 12352 null 1 470 12352 21232 0 12 12352 21314 0 8 12352 21380 0 6 12352 21669 0 12 12352 21700 0 12 12352 21731 0 12 12352 21754 0 3 12352 21755 0 6 12352 21756 0 6 12352 21770 0 2 12352 21914 0 12 12352 22064 0 12 12352 22120 0 3 12352 22138 0 3 12

##ROLLUP 
### ROLLUP performs hierarchical grouping

In [0]:
spark.sql("""
      select 
        YEAR(date) as YEAR_,
        MONTH(date) as  MONTH_,
        DAY(date) as DAY_,
        sum(quantity) as qnt
      from dfNotNull
      group by 
        rollup(
            YEAR(date), MONTH(date), DAY(date)
        )
      order by YEAR_, MONTH_, DAY_
""").display()

YEAR_ MONTH_ DAY_ qnt null null null 4906888 2010 null null 296362 2010 12 null 296362 2010 12 1 24032 2010 12 2 20855 2010 12 3 11548 2010 12 5 16394 2010 12 6 16095 2010 12 7 19351 2010 12 8 21275 2010 12 9 16904 2010 12 10 15388 2010 12 12 10561 2010 12 13 15234 2010 12 14 17108 2010 12 15 18169 2010 12 16 29482 2010 12 17 10517 2010 12 19 3735 2010 12 20 12617 2010 12 21 10888 2010 12 22 3053 2010 12 23 3156 2011 null null 4610526 2011 1 null 269379 2011 1 4 6727 2011 1 5 18155 2011 1 6 21126 2011 1 7 14437 2011 1 9 8181 2011 1 10 9363 2011 1 11 25768 2011 1 12 7781 2011 1 13 8293 2011 1 14 21050 2011 1 16 4181 2011 1 17 8662 2011 1 18 6382 2011 1 19 15786 2011 1 20 8111 2011 1 21 12440 2011 1 23 5194 2011 1 24 9542 2011 1 25 13698 2011 1 26 10392 2011 1 27 10653 2011 1 28 8511 2011 1 30 3367 2011 1 31 11579 2011 2 null 262833 2011 2 1 14867 2011 2 2 8890 2011 2 3 15370 2011 2 4 11236 2011 2 6 2048 2011 2 7 8356 2011 2 8 8645 2011 2 9 6145 2011 2 10 11348 2011 2 11 9045 2011 2 13 2715 2011 2 14 12281 2011 2 15 22079 2011 2 16 15602 2011 2 17 12758 2011 2 18 8571 2011 2 20 5346 2011 2 21 20378 2011 2 22 20877 2011 2 23 12133 2011 2 24 11512 2011 2 25 9354 2011 2 27 4858 2011 2 28 8419 2011 3 null 344012 2011 3 1 11564 2011 3 2 8529 2011 3 3 18282 2011 3 4 12934 2011 3 6 4988 2011 3 7 10920 2011 3 8 13812 2011 3 9 11484 2011 3 10 14734 2011 3 11 9215 2011 3 13 2741 2011 3 14 16719 2011 3 15 7878 2011 3 16 12549 2011 3 17 18639 2011 3 18 12969 2011 3 20 13617 2011 3 21 9346 2011 3 22 13423 2011 3 23 13951 2011 3 24 18167 2011 3 25 13273 2011 3 27 4407 2011 3 28 11301 2011 3 29 24124 2011 3 30 20049 2011 3 31 14397 2011 4 null 278585 2011 4 1 17616 2011 4 3 5648 2011 4 4 12036 2011 4 5 15280 2011 4 6 7999 2011 4 7 9981 2011 4 8 12263 2011 4 10 5526 2011 4 11 13016 2011 4 12 14450 2011 4 13 18244 2011 4 14 18143 2011 4 15 11097 2011 4 17 8181 2011 4 18 16990 2011 4 19 12824 2011 4 20 17696 2011 4 21 17056 2011 4 26 14184 2011 4 27 17627 2011 4 28 12728 2011 5 null 367852 2011 5 1 3814 2011 5 3 10981 2011 5 4 17343 2011 5 5 16079 2011 5 6 18164 2011 5 8 10692 2011 5 9 11667 2011 5 10 14364 2011 5 11 18291 2011 5 12 35674 2011 5 13 13290 2011 5 15 4771 2011 5 16 15126 2011 5 17 25058 2011 5 18 18617 2011 5 19 16690 2011 5 20 15137 2011 5 22 12736 2011 5 23 17323 2011 5 24 14401 2011 5 25 12413 2011 5 26 15991 2011 5 27 14756 2011 5 29 4084 2011 5 31 10390 2011 6 null 356922 2011 6 1 9470 2011 6 2 13569 2011 6 3 7188 2011 6 5 13470 2011 6 6 8847 2011 6 7 17589 2011 6 8 18607 2011 6 9 27134 2011 6 10 9499 2011 6 12 9479 2011 6 13 8749 2011 6 14 12856 2011 6 15 29007 2011 6 16 19592 2011 6 17 11263 2011 6 19 15060 2011 6 20 13987 2011 6 21 13023 2011 6 22 15282 2011 6 23 13591 2011 6 24 9056 2011 6 26 3495 2011 6 27 9103 2011 6 28 20798 2011 6 29 7327 2011 6 30 19881 2011 7 null 363418 2011 7 1 7015 2011 7 3 3106 2011 7 4 12040 2011 7 5 17199 2011 7 6 17768 2011 7 7 16857 2011 7 8 10095 2011 7 10 4214 2011 7 11 14075 2011 7 12 11386 2011 7 13 15192 2011 7 14 16526 2011 7 15 6127 2011 7 17 10829 2011 7 18 12078 2011 7 19 28188 2011 7 20 14626 2011 7 21 19292 2011 7 22 8298 2011 7 24 17179 2011 7 25 14223 2011 7 26 12454 2011 7 27 13222 2011 7 28 29486 2011 7 29 11085 2011 7 31 20858 2011 8 null 386612 2011 8 1 11279 2011 8 2 14131 2011 8 3 15375 2011 8 4 37779 2011 8 5 12188 2011 8 7 5079 2011 8 8 12166 2011 8 9 15623 2011 8 10 12262 2011 8 11 36602 2011 8 12 11024 2011 8 14 3135 2011 8 15 10157 2011 8 16 10449 2011 8 17 22703 2011 8 18 33854 2011 8 19 10608 2011 8 21 8158 2011 8 22 15372 2011 8 23 13640 2011 8 24 27237 2011 8 25 12879 2011 8 26 17345 2011 8 28 6770 2011 8 30 4093 2011 8 31 6704 2011 9 null 537496 2011 9 1 27828 2011 9 2 15300 2011 9 4 10883 2011 9 5 22248 2011 9 6 14340 2011 9 7 13550 2011 9 8 15771 2011 9 9 15898 2011 9 11 21122 2011 9 12 16001 2011 9 13 35021 2011 9 14 13363 2011 9 15 27525 2011 9 16 14068 2011 9 18 8966 2011 9 19 29133 2011 9 20 42626 2011 9 21 18016 2011 9 22 31950 2011 9 23 19243 2011 9 25 1932

#CUBE
CUBE performs cross grouping

In [0]:
spark.sql("""
      select 
        YEAR(date) as YEAR_,
        MONTH(date) as  MONTH_,
        DAY(date) as DAY_,
        sum(quantity) as qnt
      from dfNotNull
      group by 
        cube(
            YEAR(date), MONTH(date), DAY(date)
        )
      order by YEAR_, MONTH_, DAY_
""").display()

YEAR_ MONTH_ DAY_ qnt null null null 4906888 null null 1 168590 null null 2 141171 null null 3 145457 null null 4 186715 null null 5 215059 null null 6 192302 null null 7 202399 null null 8 171510 null null 9 164883 null null 10 159265 null null 11 189581 null null 12 130343 null null 13 156518 null null 14 180282 null null 15 163581 null null 16 157374 null null 17 187707 null null 18 164805 null null 19 150101 null null 20 203261 null null 21 176690 null null 22 152418 null null 23 143459 null null 24 148196 null null 25 147212 null null 26 109360 null null 27 136178 null null 28 172142 null null 29 98078 null null 30 113224 null null 31 79027 null 1 null 269379 null 1 4 6727 null 1 5 18155 null 1 6 21126 null 1 7 14437 null 1 9 8181 null 1 10 9363 null 1 11 25768 null 1 12 7781 null 1 13 8293 null 1 14 21050 null 1 16 4181 null 1 17 8662 null 1 18 6382 null 1 19 15786 null 1 20 8111 null 1 21 12440 null 1 23 5194 null 1 24 9542 null 1 25 13698 null 1 26 10392 null 1 27 10653 null 1 28 8511 null 1 30 3367 null 1 31 11579 null 2 null 262833 null 2 1 14867 null 2 2 8890 null 2 3 15370 null 2 4 11236 null 2 6 2048 null 2 7 8356 null 2 8 8645 null 2 9 6145 null 2 10 11348 null 2 11 9045 null 2 13 2715 null 2 14 12281 null 2 15 22079 null 2 16 15602 null 2 17 12758 null 2 18 8571 null 2 20 5346 null 2 21 20378 null 2 22 20877 null 2 23 12133 null 2 24 11512 null 2 25 9354 null 2 27 4858 null 2 28 8419 null 3 null 344012 null 3 1 11564 null 3 2 8529 null 3 3 18282 null 3 4 12934 null 3 6 4988 null 3 7 10920 null 3 8 13812 null 3 9 11484 null 3 10 14734 null 3 11 9215 null 3 13 2741 null 3 14 16719 null 3 15 7878 null 3 16 12549 null 3 17 18639 null 3 18 12969 null 3 20 13617 null 3 21 9346 null 3 22 13423 null 3 23 13951 null 3 24 18167 null 3 25 13273 null 3 27 4407 null 3 28 11301 null 3 29 24124 null 3 30 20049 null 3 31 14397 null 4 null 278585 null 4 1 17616 null 4 3 5648 null 4 4 12036 null 4 5 15280 null 4 6 7999 null 4 7 9981 null 4 8 12263 null 4 10 5526 null 4 11 13016 null 4 12 14450 null 4 13 18244 null 4 14 18143 null 4 15 11097 null 4 17 8181 null 4 18 16990 null 4 19 12824 null 4 20 17696 null 4 21 17056 null 4 26 14184 null 4 27 17627 null 4 28 12728 null 5 null 367852 null 5 1 3814 null 5 3 10981 null 5 4 17343 null 5 5 16079 null 5 6 18164 null 5 8 10692 null 5 9 11667 null 5 10 14364 null 5 11 18291 null 5 12 35674 null 5 13 13290 null 5 15 4771 null 5 16 15126 null 5 17 25058 null 5 18 18617 null 5 19 16690 null 5 20 15137 null 5 22 12736 null 5 23 17323 null 5 24 14401 null 5 25 12413 null 5 26 15991 null 5 27 14756 null 5 29 4084 null 5 31 10390 null 6 null 356922 null 6 1 9470 null 6 2 13569 null 6 3 7188 null 6 5 13470 null 6 6 8847 null 6 7 17589 null 6 8 18607 null 6 9 27134 null 6 10 9499 null 6 12 9479 null 6 13 8749 null 6 14 12856 null 6 15 29007 null 6 16 19592 null 6 17 11263 null 6 19 15060 null 6 20 13987 null 6 21 13023 null 6 22 15282 null 6 23 13591 null 6 24 9056 null 6 26 3495 null 6 27 9103 null 6 28 20798 null 6 29 7327 null 6 30 19881 null 7 null 363418 null 7 1 7015 null 7 3 3106 null 7 4 12040 null 7 5 17199 null 7 6 17768 null 7 7 16857 null 7 8 10095 null 7 10 4214 null 7 11 14075 null 7 12 11386 null 7 13 15192 null 7 14 16526 null 7 15 6127 null 7 17 10829 null 7 18 12078 null 7 19 28188 null 7 20 14626 null 7 21 19292 null 7 22 8298 null 7 24 17179 null 7 25 14223 null 7 26 12454 null 7 27 13222 null 7 28 29486 null 7 29 11085 null 7 31 20858 null 8 null 386612 null 8 1 11279 null 8 2 14131 null 8 3 15375 null 8 4 37779 null 8 5 12188 null 8 7 5079 null 8 8 12166 null 8 9 15623 null 8 10 12262 null 8 11 36602 null 8 12 11024 null 8 14 3135 null 8 15 10157 null 8 16 10449 null 8 17 22703 null 8 18 33854 null 8 19 10608 null 8 21 8158 null 8 22 15372 null 8 23 13640 null 8 24 27237 null 8 25 12879 null 8 26 17345 null 8 28 6770 null 8 30 4093 null 8 31 6704 null 9 null 537496 null 9 1 27828 null 9 2 15300 null 9 4 10883 null 9 5 22248 null 9 6 14340 null 9 7 13550 null 9 8 15771 null 

# pivot

In [0]:
data = [
    ("A", "X", 10),
    ("A", "Y", 20),
    ("B", "X", 30),
    ("B", "Y", 40)
]
dataframe = (
    spark.createDataFrame(data, ['id','categ','value'])
)
display(dataframe)

id categ value A X 10 A Y 20 B X 30 B Y 40

In [0]:
pivoted_df = (
    dataframe.groupBy('id').pivot('categ').sum('value')

)

display(pivoted_df)

id X Y B 30 40 A 10 20